   # 爬蟲架構

In [ ]:
#上層爬蟲:處理換頁、資料總筆數問題

In [ ]:
#中層爬蟲:處理單一頁面內每筆資料頁面(URL)連結問題

In [ ]:
#下層爬蟲:清理資料，放入DIST。

In [8]:
import requests
from bs4 import BeautifulSoup

In [9]:
HOST = 'https://www.ptt.cc'


In [19]:
list_ptt = []

#def crawl_ptt(no_pages):
def crawl_ptt(board_name, no_pages):
    res = requests.get(HOST + "/bbs/" + board_name + "/index.html")
    soup = BeautifulSoup(res.text, 'lxml')
    total_page = int(soup.select('a.wide')[1]['href'].split('index')[1].split('.html')[0]) + 1

    for page in range(total_page, total_page - no_pages, -1):
        url = HOST + "/bbs/{}/index{}.html".format(board_name,page)
        print(url)
        list_crawler(url)
        crawler_writer(board_name)
    
def list_crawler(url):
    res_ls = requests.get(url)
    soup_ls = BeautifulSoup(res_ls.text, 'lxml')
    for tag in soup_ls.select('div.title > a'):
        title = tag.text
        url_ls = HOST + tag['href']
        print(url_ls)        
        article_crawler(url_ls)
    
def article_crawler(url_ls):    
    res_article = requests.get(url_ls)
    soup_article = BeautifulSoup(res_article.text, 'lxml')
#    print(soup_article)
    article_dict = {}
    
    meta_values = soup_article.select('span.article-meta-value')
    try:
        article_dict['author'] = meta_values[0].text
        article_dict['board'] = meta_values[1].text
        article_dict['title'] = meta_values[2].text
        article_dict['tm'] = meta_values[3].text
    except IndexError:
       pass
    
    pushs = []
    try:
        for push in soup_article.select('div.push'):
            push_dict = {}
            push_spans = push.select('span')
            if push_spans[0] != "":
                push_dict['push_type'] = push_spans[0].text.strip()
            if push_spans[1] != "":
                push_dict['push_author'] = push_spans[1].text.strip()
            if push_spans[2] != "":
                push_dict['push_content'] = push_spans[2].text.split(': ')[1].strip()
            if push_spans[3] != "":
                push_dict['push_tm'] = push_spans[3].text.strip()
            pushs.append(push_dict)
            article_dict['pushs'] = pushs

        for tag in soup_article.select('span.article-meta-value'):
            tag.extract()
        for tag in soup_article.select('span.article-meta-tag'):
            tag.extract()
        for tag in soup_article.select('span.f2'):
            tag.extract()
        for tag in soup_article.select('div.push'):
            tag.extract()
        article_dict['content'] = soup_article.select_one("#main-content").text.strip()    
        print(article_dict)
    except IndexError:
       pass
    
    list_ptt.append(article_dict)
    
def crawler_writer(board_name):
    with open('./list_ptt_{}.txt'.format(board_name), 'w', encoding='utf-8') as f:
     for posts in list_ptt:
        f.write('\n')
        for keys in posts:
            valus_str = "{} : {}".format(keys, str(posts[keys]))
            f.write(valus_str + '\n')

In [27]:
crawl_ptt('ObataTakeshi',1)

https://www.ptt.cc/bbs/ObataTakeshi/index52.html
https://www.ptt.cc/bbs/ObataTakeshi/M.1456976001.A.3D9.html
{'pushs': [{'push_tm': '03/07 07:42', 'push_type': '→', 'push_content': '覺得近期老師合作的作品節奏都有點怪…這篇鉑金也是', 'push_author': 'ltsart0515'}, {'push_tm': '03/17 00:46', 'push_type': '推', 'push_content': '怎麼辦覺得不太好看...', 'push_author': 'amy29585028'}], 'content': '鉑金終局Platinum End 第5話『發表的瞬間』\njn3b3zx\n\n--\n請低調推\n\n--', 'title': '[低調] 鉑金終局Platinum End 第5話', 'board': 'ObataTakeshi', 'author': 'jou705 ((．＿．?))', 'tm': 'Thu Mar  3 11:33:19 2016'}
https://www.ptt.cc/bbs/ObataTakeshi/M.1459527591.A.A71.html
{'pushs': [{'push_tm': '04/02 00:26', 'push_type': '推', 'push_content': '等好久啦～～～～～～～～～～～', 'push_author': 'iambling'}, {'push_tm': '04/02 11:06', 'push_type': '推', 'push_content': 'QAQ', 'push_author': 'bohun'}, {'push_tm': '04/02 17:29', 'push_type': '推', 'push_content': 'thanks!', 'push_author': 'mythnc'}], 'content': '鉑金終局Platinum End 第6話『私下的話』\nglyspzg\n\n--\n請低調推\n\n--', 'title': '[低調] 鉑金終

In [24]:
list_ptt

[{'author': 'jou705 ((．＿．?))',
  'board': 'ObataTakeshi',
  'content': '鉑金終局Platinum End 第5話『發表的瞬間』\njn3b3zx\n\n--\n請低調推\n\n--',
  'pushs': [{'push_author': 'ltsart0515',
    'push_content': '覺得近期老師合作的作品節奏都有點怪…這篇鉑金也是',
    'push_tm': '03/07 07:42',
    'push_type': '→'},
   {'push_author': 'amy29585028',
    'push_content': '怎麼辦覺得不太好看...',
    'push_tm': '03/17 00:46',
    'push_type': '推'}],
  'title': '[低調] 鉑金終局Platinum End 第5話',
  'tm': 'Thu Mar  3 11:33:19 2016'},
 {'author': 'jou705 ((．＿．?))',
  'board': 'ObataTakeshi',
  'content': '鉑金終局Platinum End 第6話『私下的話』\nglyspzg\n\n--\n請低調推\n\n--',
  'pushs': [{'push_author': 'iambling',
    'push_content': '等好久啦～～～～～～～～～～～',
    'push_tm': '04/02 00:26',
    'push_type': '推'},
   {'push_author': 'bohun',
    'push_content': 'QAQ',
    'push_tm': '04/02 11:06',
    'push_type': '推'},
   {'push_author': 'mythnc',
    'push_content': 'thanks!',
    'push_tm': '04/02 17:29',
    'push_type': '推'}],
  'title': '[低調] 鉑金終局Platinum End 第6話',
  'tm

In [25]:
crawler_writer()

NameError: name 'board_name' is not defined

In [8]:
with open('./list_ptt.txt', 'w', encoding='utf-8') as f:
     for posts in list_ptt:
        f.write('\n')
        for keys in posts:
            valus_str = "{} : {}".format(keys, str(posts[keys]))
            f.write(valus_str + '\n')
   

In [ ]:
crawl_ptt('WomenTalk',4999)

https://www.ptt.cc/bbs/WomenTalk/index5000.html
https://www.ptt.cc/bbs/WomenTalk/M.1482757931.A.03E.html
{'content': '黨工好閒 長文消毒\n\n\n看過"辛德勒的名單"嗎?\n\n\n種族清洗\n\n被你說的好像沒什麼\n\n\n\n真的好會講\n\n\n\n戰爭爆發的時候 看你會不會這麼會講?\n\n\n: 先說我很討厭猶太人跟跟風的人\n: 所以我接下來講的可能不會太客觀\n: 你大可以不要看因為一點也不中肯\n: 不過我主要要講的是法學的言論自由還有我對這件事在教育層面的看法\n: 首先我們要先來講言論自由這一塊\n: 世界上言論主要分兩個體系\n: 第一個是歐洲體系\n: 他們對於言論自由的審查是事前審查\n: 簡單來說就是國家在你發表言論前就得審核你可不可以說\n: 換個角度來說就是政府規定什麼不能說就是真的不能說\n: 為什麼會這樣原因很簡單\n: 因為納粹的關係全歐洲都怕\n: 所以在歐洲只要出現一丁點納粹的東西代志都很大條\n: 因為這一塊你是不能主張言論自由的\n: 另一套系統是老美的\n: 他們比較複雜\n: 原則上還是採事後審查制\n: 就是你講完再探討合不合法\n: 他們採納的是雙階理論twotrack theory\n: 內容限制和非內容限制\n: 內容限制政府規定哪些言論不得主張發表\n: 反之\n: 非內容限制是限制表達的方式和管道\n: 內容限制又可以分高價值低價值\n: 高價值理論主要指明顯而立即危險\n: 就像你在臉書說你要炸穿普阿媽家\n: 低價值言論比較實務像商業猥褻誹謗\n: 就像我是金城武這樣\n: 高價值言論審查比較不嚴格低價值言論比較不嚴格\n: 用ptt來比喻高價值就像這裡的版規低價值就像八卦版版規一樣\n: 講到這裡\n: 有沒有發現台灣的言論自由比較像美國的\n: 我們很多言論自由釋字都是參考美國法\n: 所以問題來了\n: 我們為什麼在這件事要用德國言論自由的審查機制來審查這些高中生\n: 以色列德國對台灣有管轄權？\n: 我們國家有自己國家的言論自由審查機制\n: 行的正做的直德國憑什麼管\n: 在台灣這些高中生就是有言論自由\n: 我們要怎麼事後審查是我們自己的事\n: 法律就是保障他有人權

In [23]:
crawler_writer('WomenTalk')